
# 通过信息准则进行Lasso模型选择

本示例重现了[ZHT2007]_中图2的示例。一个
:class:`~sklearn.linear_model.LassoLarsIC` 估计器在糖尿病数据集上进行拟合，并使用AIC和BIC准则选择最佳模型。

.. NOTE::
    需要注意的是，使用:class:`~sklearn.linear_model.LassoLarsIC` 找到 `alpha` 的优化依赖于在样本内计算的AIC或BIC准则，因此直接在训练集上进行。这种方法不同于交叉验证程序。关于这两种方法的比较，可以参考以下示例：
    `sphx_glr_auto_examples_linear_model_plot_lasso_model_selection.py` .

.. rubric:: References

.. [ZHT2007] :arxiv:`Zou, Hui, Trevor Hastie, and Robert Tibshirani.
    "On the degrees of freedom of the lasso."
    The Annals of Statistics 35.5 (2007): 2173-2192.
    <0712.0881>` 


In [ ]:
# 作者：scikit-learn 开发者
# SPDX 许可证标识符：BSD-3-Clause

我们将使用糖尿病数据集。



In [ ]:
from sklearn.datasets import load_diabetes

X, y = load_diabetes(return_X_y=True, as_frame=True)
n_samples = X.shape[0]
X.head()

Scikit-learn 提供了一个名为 :class:`~sklearn.linear_model.LassoLarsIC` 的估计器，该估计器使用赤池信息准则 (AIC) 或贝叶斯信息准则 (BIC) 来选择最佳模型。在拟合此模型之前，我们将对数据集进行缩放。

接下来，我们将拟合两个模型，以比较AIC和BIC报告的值。



In [ ]:
from sklearn.linear_model import LassoLarsIC
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler

lasso_lars_ic = make_pipeline(StandardScaler(), LassoLarsIC(criterion="aic")).fit(X, y)

为了与 [ZHT2007]_ 中的定义保持一致，我们需要重新调整 AIC 和 BIC 的尺度。实际上，Zou 等人忽略了一些常数项，这些常数项与从线性模型的最大对数似然推导出的 AIC 原始定义相比。您可以参考 `用户指南的数学细节部分 <lasso_lars_ic>` 。



In [ ]:
def zou_et_al_criterion_rescaling(criterion, n_samples, noise_variance):
    """将信息准则重新调整为符合Zou等人的定义。"""
    return criterion - n_samples * np.log(2 * np.pi * noise_variance) - n_samples

In [ ]:
import numpy as np

aic_criterion = zou_et_al_criterion_rescaling(
    lasso_lars_ic[-1].criterion_,
    n_samples,
    lasso_lars_ic[-1].noise_variance_,
)

index_alpha_path_aic = np.flatnonzero(
    lasso_lars_ic[-1].alphas_ == lasso_lars_ic[-1].alpha_
)[0]

In [ ]:
lasso_lars_ic.set_params(lassolarsic__criterion="bic").fit(X, y)

bic_criterion = zou_et_al_criterion_rescaling(
    lasso_lars_ic[-1].criterion_,
    n_samples,
    lasso_lars_ic[-1].noise_variance_,
)

index_alpha_path_bic = np.flatnonzero(
    lasso_lars_ic[-1].alphas_ == lasso_lars_ic[-1].alpha_
)[0]

现在我们已经收集了AIC和BIC，我们可以检查两个准则的最小值是否发生在相同的alpha值处。然后，我们可以简化下面的图表。



In [ ]:
index_alpha_path_aic == index_alpha_path_bic

最终，我们可以绘制AIC和BIC准则以及随后的选择正则化参数。



In [ ]:
import matplotlib.pyplot as plt

plt.plot(aic_criterion, color="tab:blue", marker="o", label="AIC criterion")
plt.plot(bic_criterion, color="tab:orange", marker="o", label="BIC criterion")
plt.vlines(
    index_alpha_path_bic,
    aic_criterion.min(),
    aic_criterion.max(),
    color="black",
    linestyle="--",
    label="Selected alpha",
)
plt.legend()
plt.ylabel("Information criterion")
plt.xlabel("Lasso model sequence")
_ = plt.title("Lasso model selection via AIC and BIC")